In [1]:
%config Completer.use_jedi = False

import configparser
config = configparser.ConfigParser()
config.read('XXX-config.txt')

source_folder = config.get('Configuration', 'source_folder')
time_step = int(config.get('Configuration', 'time_step'))
window_size = int(config.get('Configuration', 'window_size'))
data_folder = config.get('Configuration', 'data_folder')
ini_date = config.get('Configuration', 'ini_date')
end_date = config.get('Configuration', 'end_date')

users=config.get('Configuration', 'users')
users = [(item.strip()) for item in users.split(',')]

w = int(config.get('Configuration', 'w'))
h = int(config.get('Configuration', 'h'))

anchors=config.get('Configuration', 'anchors')
anchors = [(item.strip()) for item in anchors.split(',')]

rooms=config.get('Configuration', 'rooms')
rooms = [(item.strip()) for item in rooms.split(',')]

In [2]:
import pandas as pd
import collections
import math
import os

import cv2
import matplotlib.pyplot as plt
import cv2
import sys
import numpy as np
import math
import time
from PIL import Image 
import shutil

from pandas import read_csv  



In [3]:
import numpy as np
from pandas import read_csv    
import pandas as pd
import time

from datetime import datetime

off_zone=60*60*2

def day_time(ti):
    return int((int)((ti+off_zone)/(60*60*24)))


def time2str(tt):
    return datetime.fromtimestamp(tt).strftime("%Y-%m-%d %H:%M:%S")


t0 = (int)(datetime.strptime(ini_date, '%Y-%m-%d %H:%M:%S').timestamp())
print (ini_date,"Init date is", t0, "day:",day_time(t0), time2str(t0))

tN = (int)(datetime.strptime(end_date, '%Y-%m-%d %H:%M:%S').timestamp())
print (end_date,"End date is", tN, "day:",day_time(tN), time2str(tN))


def day_time0(ti):
    return day_time(ti)-day_time(t0)+1

def relT(ti):
    return (int)((ti-t0)/time_step)

day=list(range(day_time(t0),day_time(tN)+1))[0]
day=19798
print(day)

1980-01-01 13:00:02 Init date is 315576002 day: 3652 1980-01-01 13:00:02
1980-01-01 14:51:20 End date is 315582680 day: 3652 1980-01-01 14:51:20
19798


In [4]:
import os

df_total_map = {}
for room in rooms:
    df_total_map[room]={}
    print(os.listdir(os.path.join(source_folder,room)))
    for user in users:
        df_total_map[room][user]=None
        
    for person in os.listdir(os.path.join(source_folder,room)):
        for scene in os.listdir(os.path.join(source_folder,room,person)):
            print("scene",scene)
            for user in users:                
                print(os.path.join(source_folder,room,person,scene)+"/ubitrack-uwb/"+str(day)+"."+user+".sourcedata.tsv")
                try:
                    series=read_csv(os.path.join(source_folder,room,person,scene)+"/ubitrack-uwb/"+str(day)+"."+user+".sourcedata.tsv", sep="\t",parse_dates=True, header=None, names=["time","date","anchor","d"])
                    print(day,series.size)
                except Exception as e:
                    print("Not data",e)
                    continue
                if(df_total_map[room][user] is None):
                    df_total_map[room][user]=series
                else:
                    df_total_map[room][user] = df_total_map[room][user].append(series, ignore_index=True)

['1-person-labelled', '2-person-labelled', '3-person-labelled']
scene Scene1
./data/-aligned/livingroom\1-person-labelled\Scene1/ubitrack-uwb/19798.f02e.sourcedata.tsv
Not data [Errno 2] No such file or directory: './data/-aligned/livingroom\\1-person-labelled\\Scene1/ubitrack-uwb/19798.f02e.sourcedata.tsv'
./data/-aligned/livingroom\1-person-labelled\Scene1/ubitrack-uwb/19798.867f.sourcedata.tsv
Not data [Errno 2] No such file or directory: './data/-aligned/livingroom\\1-person-labelled\\Scene1/ubitrack-uwb/19798.867f.sourcedata.tsv'
./data/-aligned/livingroom\1-person-labelled\Scene1/ubitrack-uwb/19798.ed9c.sourcedata.tsv
19798 2400
scene Scene2
./data/-aligned/livingroom\1-person-labelled\Scene2/ubitrack-uwb/19798.f02e.sourcedata.tsv
Not data [Errno 2] No such file or directory: './data/-aligned/livingroom\\1-person-labelled\\Scene2/ubitrack-uwb/19798.f02e.sourcedata.tsv'
./data/-aligned/livingroom\1-person-labelled\Scene2/ubitrack-uwb/19798.867f.sourcedata.tsv
Not data [Errno 2] No

C:\Users\javie\AppData\Local\Temp\ipykernel_26528\1955475338.py:24: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_total_map[room][user] = df_total_map[room][user].append(series, ignore_index=True)
C:\Users\javie\AppData\Local\Temp\ipykernel_26528\1955475338.py:24: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_total_map[room][user] = df_total_map[room][user].append(series, ignore_index=True)
C:\Users\javie\AppData\Local\Temp\ipykernel_26528\1955475338.py:24: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_total_map[room][user] = df_total_map[room][user].append(series, ignore_index=True)
C:\Users\javie\AppData\Local\Temp\ipykernel_26528\1955475338.py:24: FutureWarning: The frame.append method is deprecated and will be 

In [5]:
import cv2
import os


for user in users:
    for anchor in anchors:
        filew = open(data_folder+"/DAY_"+str(day)+"/"+user+"."+anchor+".tsv", "w")
   
        for tt in range(t0,tN,time_step):
            print(tt,time2str(tt),anchor)
            #if(day_time(tt) != day):
            #    continue

            min_v=10
            max_v=-10
            for room in rooms:
                df_total=df_total_map[room][user]
                #print(df_total)
                df_intervalo = df_total[(df_total['time'] >= (tt-1)) & (df_total['time'] <= (tt)) & (df_total['anchor'] ==anchor) ]
                if(df_intervalo.size>0):
                    min_v=min(min_v,np.min(df_intervalo['d']))
                    max_v=max(max_v,np.max(df_intervalo['d']))

            filew.write(str(tt)+"\t"+str(min_v)+"\t"+str(max_v)+"\n")
        filew.close()


315576002 1980-01-01 13:00:02 8171
315576003 1980-01-01 13:00:03 8171
315576004 1980-01-01 13:00:04 8171
315576005 1980-01-01 13:00:05 8171
315576006 1980-01-01 13:00:06 8171
315576007 1980-01-01 13:00:07 8171
315576008 1980-01-01 13:00:08 8171
315576009 1980-01-01 13:00:09 8171
315576010 1980-01-01 13:00:10 8171
315576011 1980-01-01 13:00:11 8171
315576012 1980-01-01 13:00:12 8171
315576013 1980-01-01 13:00:13 8171
315576014 1980-01-01 13:00:14 8171
315576015 1980-01-01 13:00:15 8171
315576016 1980-01-01 13:00:16 8171
315576017 1980-01-01 13:00:17 8171
315576018 1980-01-01 13:00:18 8171
315576019 1980-01-01 13:00:19 8171
315576020 1980-01-01 13:00:20 8171
315576021 1980-01-01 13:00:21 8171
315576022 1980-01-01 13:00:22 8171
315576023 1980-01-01 13:00:23 8171
315576024 1980-01-01 13:00:24 8171
315576025 1980-01-01 13:00:25 8171
315576026 1980-01-01 13:00:26 8171
315576027 1980-01-01 13:00:27 8171
315576028 1980-01-01 13:00:28 8171
315576029 1980-01-01 13:00:29 8171
315576030 1980-01-01

315576333 1980-01-01 13:05:33 8171
315576334 1980-01-01 13:05:34 8171
315576335 1980-01-01 13:05:35 8171
315576336 1980-01-01 13:05:36 8171
315576337 1980-01-01 13:05:37 8171
315576338 1980-01-01 13:05:38 8171
315576339 1980-01-01 13:05:39 8171
315576340 1980-01-01 13:05:40 8171
315576341 1980-01-01 13:05:41 8171
315576342 1980-01-01 13:05:42 8171
315576343 1980-01-01 13:05:43 8171
315576344 1980-01-01 13:05:44 8171
315576345 1980-01-01 13:05:45 8171
315576346 1980-01-01 13:05:46 8171
315576347 1980-01-01 13:05:47 8171
315576348 1980-01-01 13:05:48 8171
315576349 1980-01-01 13:05:49 8171
315576350 1980-01-01 13:05:50 8171
315576351 1980-01-01 13:05:51 8171
315576352 1980-01-01 13:05:52 8171
315576353 1980-01-01 13:05:53 8171
315576354 1980-01-01 13:05:54 8171
315576355 1980-01-01 13:05:55 8171
315576356 1980-01-01 13:05:56 8171
315576357 1980-01-01 13:05:57 8171
315576358 1980-01-01 13:05:58 8171
315576359 1980-01-01 13:05:59 8171
315576360 1980-01-01 13:06:00 8171
315576361 1980-01-01

315576653 1980-01-01 13:10:53 8171
315576654 1980-01-01 13:10:54 8171
315576655 1980-01-01 13:10:55 8171
315576656 1980-01-01 13:10:56 8171
315576657 1980-01-01 13:10:57 8171
315576658 1980-01-01 13:10:58 8171
315576659 1980-01-01 13:10:59 8171
315576660 1980-01-01 13:11:00 8171
315576661 1980-01-01 13:11:01 8171
315576662 1980-01-01 13:11:02 8171
315576663 1980-01-01 13:11:03 8171
315576664 1980-01-01 13:11:04 8171
315576665 1980-01-01 13:11:05 8171
315576666 1980-01-01 13:11:06 8171
315576667 1980-01-01 13:11:07 8171
315576668 1980-01-01 13:11:08 8171
315576669 1980-01-01 13:11:09 8171
315576670 1980-01-01 13:11:10 8171
315576671 1980-01-01 13:11:11 8171
315576672 1980-01-01 13:11:12 8171
315576673 1980-01-01 13:11:13 8171
315576674 1980-01-01 13:11:14 8171
315576675 1980-01-01 13:11:15 8171
315576676 1980-01-01 13:11:16 8171
315576677 1980-01-01 13:11:17 8171
315576678 1980-01-01 13:11:18 8171
315576679 1980-01-01 13:11:19 8171
315576680 1980-01-01 13:11:20 8171
315576681 1980-01-01

315576996 1980-01-01 13:16:36 8171
315576997 1980-01-01 13:16:37 8171
315576998 1980-01-01 13:16:38 8171
315576999 1980-01-01 13:16:39 8171
315577000 1980-01-01 13:16:40 8171
315577001 1980-01-01 13:16:41 8171
315577002 1980-01-01 13:16:42 8171
315577003 1980-01-01 13:16:43 8171
315577004 1980-01-01 13:16:44 8171
315577005 1980-01-01 13:16:45 8171
315577006 1980-01-01 13:16:46 8171
315577007 1980-01-01 13:16:47 8171
315577008 1980-01-01 13:16:48 8171
315577009 1980-01-01 13:16:49 8171
315577010 1980-01-01 13:16:50 8171
315577011 1980-01-01 13:16:51 8171
315577012 1980-01-01 13:16:52 8171
315577013 1980-01-01 13:16:53 8171
315577014 1980-01-01 13:16:54 8171
315577015 1980-01-01 13:16:55 8171
315577016 1980-01-01 13:16:56 8171
315577017 1980-01-01 13:16:57 8171
315577018 1980-01-01 13:16:58 8171
315577019 1980-01-01 13:16:59 8171
315577020 1980-01-01 13:17:00 8171
315577021 1980-01-01 13:17:01 8171
315577022 1980-01-01 13:17:02 8171
315577023 1980-01-01 13:17:03 8171
315577024 1980-01-01

315577328 1980-01-01 13:22:08 8171
315577329 1980-01-01 13:22:09 8171
315577330 1980-01-01 13:22:10 8171
315577331 1980-01-01 13:22:11 8171
315577332 1980-01-01 13:22:12 8171
315577333 1980-01-01 13:22:13 8171
315577334 1980-01-01 13:22:14 8171
315577335 1980-01-01 13:22:15 8171
315577336 1980-01-01 13:22:16 8171
315577337 1980-01-01 13:22:17 8171
315577338 1980-01-01 13:22:18 8171
315577339 1980-01-01 13:22:19 8171
315577340 1980-01-01 13:22:20 8171
315577341 1980-01-01 13:22:21 8171
315577342 1980-01-01 13:22:22 8171
315577343 1980-01-01 13:22:23 8171
315577344 1980-01-01 13:22:24 8171
315577345 1980-01-01 13:22:25 8171
315577346 1980-01-01 13:22:26 8171
315577347 1980-01-01 13:22:27 8171
315577348 1980-01-01 13:22:28 8171
315577349 1980-01-01 13:22:29 8171
315577350 1980-01-01 13:22:30 8171
315577351 1980-01-01 13:22:31 8171
315577352 1980-01-01 13:22:32 8171
315577353 1980-01-01 13:22:33 8171
315577354 1980-01-01 13:22:34 8171
315577355 1980-01-01 13:22:35 8171
315577356 1980-01-01

...

315581599 1980-01-01 14:33:19 c492
315581600 1980-01-01 14:33:20 c492
315581601 1980-01-01 14:33:21 c492
315581602 1980-01-01 14:33:22 c492
315581603 1980-01-01 14:33:23 c492
315581604 1980-01-01 14:33:24 c492
315581605 1980-01-01 14:33:25 c492
315581606 1980-01-01 14:33:26 c492
315581607 1980-01-01 14:33:27 c492
315581608 1980-01-01 14:33:28 c492
315581609 1980-01-01 14:33:29 c492
315581610 1980-01-01 14:33:30 c492
315581611 1980-01-01 14:33:31 c492
315581612 1980-01-01 14:33:32 c492
315581613 1980-01-01 14:33:33 c492
315581614 1980-01-01 14:33:34 c492
315581615 1980-01-01 14:33:35 c492
315581616 1980-01-01 14:33:36 c492
315581617 1980-01-01 14:33:37 c492
315581618 1980-01-01 14:33:38 c492
315581619 1980-01-01 14:33:39 c492
315581620 1980-01-01 14:33:40 c492
315581621 1980-01-01 14:33:41 c492
315581622 1980-01-01 14:33:42 c492
315581623 1980-01-01 14:33:43 c492
315581624 1980-01-01 14:33:44 c492
315581625 1980-01-01 14:33:45 c492
315581626 1980-01-01 14:33:46 c492
315581627 1980-01-01

315581849 1980-01-01 14:37:29 c492
315581850 1980-01-01 14:37:30 c492
315581851 1980-01-01 14:37:31 c492
315581852 1980-01-01 14:37:32 c492
315581853 1980-01-01 14:37:33 c492
315581854 1980-01-01 14:37:34 c492
315581855 1980-01-01 14:37:35 c492
315581856 1980-01-01 14:37:36 c492
315581857 1980-01-01 14:37:37 c492
315581858 1980-01-01 14:37:38 c492
315581859 1980-01-01 14:37:39 c492
315581860 1980-01-01 14:37:40 c492
315581861 1980-01-01 14:37:41 c492
315581862 1980-01-01 14:37:42 c492
315581863 1980-01-01 14:37:43 c492
315581864 1980-01-01 14:37:44 c492
315581865 1980-01-01 14:37:45 c492
315581866 1980-01-01 14:37:46 c492
315581867 1980-01-01 14:37:47 c492
315581868 1980-01-01 14:37:48 c492
315581869 1980-01-01 14:37:49 c492
315581870 1980-01-01 14:37:50 c492
315581871 1980-01-01 14:37:51 c492
315581872 1980-01-01 14:37:52 c492
315581873 1980-01-01 14:37:53 c492
315581874 1980-01-01 14:37:54 c492
315581875 1980-01-01 14:37:55 c492
315581876 1980-01-01 14:37:56 c492
315581877 1980-01-01

315582118 1980-01-01 14:41:58 c492
315582119 1980-01-01 14:41:59 c492
315582120 1980-01-01 14:42:00 c492
315582121 1980-01-01 14:42:01 c492
315582122 1980-01-01 14:42:02 c492
315582123 1980-01-01 14:42:03 c492
315582124 1980-01-01 14:42:04 c492
315582125 1980-01-01 14:42:05 c492
315582126 1980-01-01 14:42:06 c492
315582127 1980-01-01 14:42:07 c492
315582128 1980-01-01 14:42:08 c492
315582129 1980-01-01 14:42:09 c492
315582130 1980-01-01 14:42:10 c492
315582131 1980-01-01 14:42:11 c492
315582132 1980-01-01 14:42:12 c492
315582133 1980-01-01 14:42:13 c492
315582134 1980-01-01 14:42:14 c492
315582135 1980-01-01 14:42:15 c492
315582136 1980-01-01 14:42:16 c492
315582137 1980-01-01 14:42:17 c492
315582138 1980-01-01 14:42:18 c492
315582139 1980-01-01 14:42:19 c492
315582140 1980-01-01 14:42:20 c492
315582141 1980-01-01 14:42:21 c492
315582142 1980-01-01 14:42:22 c492
315582143 1980-01-01 14:42:23 c492
315582144 1980-01-01 14:42:24 c492
315582145 1980-01-01 14:42:25 c492
315582146 1980-01-01

315582363 1980-01-01 14:46:03 c492
315582364 1980-01-01 14:46:04 c492
315582365 1980-01-01 14:46:05 c492
315582366 1980-01-01 14:46:06 c492
315582367 1980-01-01 14:46:07 c492
315582368 1980-01-01 14:46:08 c492
315582369 1980-01-01 14:46:09 c492
315582370 1980-01-01 14:46:10 c492
315582371 1980-01-01 14:46:11 c492
315582372 1980-01-01 14:46:12 c492
315582373 1980-01-01 14:46:13 c492
315582374 1980-01-01 14:46:14 c492
315582375 1980-01-01 14:46:15 c492
315582376 1980-01-01 14:46:16 c492
315582377 1980-01-01 14:46:17 c492
315582378 1980-01-01 14:46:18 c492
315582379 1980-01-01 14:46:19 c492
315582380 1980-01-01 14:46:20 c492
315582381 1980-01-01 14:46:21 c492
315582382 1980-01-01 14:46:22 c492
315582383 1980-01-01 14:46:23 c492
315582384 1980-01-01 14:46:24 c492
315582385 1980-01-01 14:46:25 c492
315582386 1980-01-01 14:46:26 c492
315582387 1980-01-01 14:46:27 c492
315582388 1980-01-01 14:46:28 c492
315582389 1980-01-01 14:46:29 c492
315582390 1980-01-01 14:46:30 c492
315582391 1980-01-01

315582608 1980-01-01 14:50:08 c492
315582609 1980-01-01 14:50:09 c492
315582610 1980-01-01 14:50:10 c492
315582611 1980-01-01 14:50:11 c492
315582612 1980-01-01 14:50:12 c492
315582613 1980-01-01 14:50:13 c492
315582614 1980-01-01 14:50:14 c492
315582615 1980-01-01 14:50:15 c492
315582616 1980-01-01 14:50:16 c492
315582617 1980-01-01 14:50:17 c492
315582618 1980-01-01 14:50:18 c492
315582619 1980-01-01 14:50:19 c492
315582620 1980-01-01 14:50:20 c492
315582621 1980-01-01 14:50:21 c492
315582622 1980-01-01 14:50:22 c492
315582623 1980-01-01 14:50:23 c492
315582624 1980-01-01 14:50:24 c492
315582625 1980-01-01 14:50:25 c492
315582626 1980-01-01 14:50:26 c492
315582627 1980-01-01 14:50:27 c492
315582628 1980-01-01 14:50:28 c492
315582629 1980-01-01 14:50:29 c492
315582630 1980-01-01 14:50:30 c492
315582631 1980-01-01 14:50:31 c492
315582632 1980-01-01 14:50:32 c492
315582633 1980-01-01 14:50:33 c492
315582634 1980-01-01 14:50:34 c492
315582635 1980-01-01 14:50:35 c492
315582636 1980-01-01

In [6]:
print(min_v,max_v)

4.205 4.205


In [7]:
df_total=df_total_map["livingroom"]["f02e"]
print(df_total)
print(anchor)
anchor="8171"
tt=1710613800
df_intervalo = df_total[(df_total['time'] >= (tt-1)) & (df_total['time'] <= (tt)) & (df_total['anchor'] ==anchor) ]

print(df_intervalo)

           time                 date anchor      d
0     315577972  1980-01-01 13:32:52   8171  5.147
1     315577972  1980-01-01 13:32:52   2eff  5.784
2     315577972  1980-01-01 13:32:52   eb38  3.699
3     315577972  1980-01-01 13:32:52   8171  5.156
4     315577972  1980-01-01 13:32:52   2eff  5.817
...         ...                  ...    ...    ...
5779  315580330  1980-01-01 14:12:10   a304  8.699
5780  315580330  1980-01-01 14:12:10   8171  4.528
5781  315580330  1980-01-01 14:12:10   2eff  7.573
5782  315580330  1980-01-01 14:12:10   eb38  3.610
5783  315580330  1980-01-01 14:12:10   a304  8.717

[5784 rows x 4 columns]
c492
Empty DataFrame
Columns: [time, date, anchor, d]
Index: []
